In [3]:
%matplotlib inline
import numpy as np
import pandas as pd
import re as re

train = pd.read_csv('train.csv', header = 0, dtype={'Age': np.float64})
test  = pd.read_csv('test.csv' , header = 0, dtype={'Age': np.float64})
full_data = [train, test]

print (train.info())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 891 entries, 0 to 890
Data columns (total 12 columns):
PassengerId    891 non-null int64
Survived       891 non-null int64
Pclass         891 non-null int64
Name           891 non-null object
Sex            891 non-null object
Age            714 non-null float64
SibSp          891 non-null int64
Parch          891 non-null int64
Ticket         891 non-null object
Fare           891 non-null float64
Cabin          204 non-null object
Embarked       889 non-null object
dtypes: float64(2), int64(5), object(5)
memory usage: 90.5+ KB
None


# Feature Engineering


## Pclass


In [4]:
train[["Pclass", "Survived"]].groupby("Pclass").mean()


Survived
Pclass          
1       0.629630
2       0.472826
3       0.242363

## Sex

In [5]:
train[["Sex", "Survived"]].groupby("Sex").mean()


Survived
Sex             
female  0.742038
male    0.188908

## Parch and SibSp

In [6]:
for dataset in full_data:
    dataset['FamilySize'] = dataset['SibSp'] + dataset['Parch'] + 1
print (train[['FamilySize', 'Survived']].groupby(['FamilySize'], as_index=False).mean())


   FamilySize  Survived
0           1  0.303538
1           2  0.552795
2           3  0.578431
3           4  0.724138
4           5  0.200000
5           6  0.136364
6           7  0.333333
7           8  0.000000
8          11  0.000000


In [7]:


for dataset in full_data:
    dataset['IsAlone'] = 0
    dataset.loc[dataset['FamilySize'] == 1, 'IsAlone'] = 1
print (train[['IsAlone', 'Survived']].groupby(['IsAlone'], as_index=False).mean())



   IsAlone  Survived
0        0  0.505650
1        1  0.303538


## Embarked

In [8]:
for dataset in full_data:
    dataset['Embarked'] = dataset['Embarked'].fillna('S')
print (train[['Embarked', 'Survived']].groupby(['Embarked'], as_index=False).mean())


  Embarked  Survived
0        C  0.553571
1        Q  0.389610
2        S  0.339009


## Fare
Fill the missing values with median

In [9]:
for dataset in full_data:
#     dataset['Fare'] = dataset['Fare'][dataset['Fare']].astype(int)
    dataset['Fare'] = dataset['Fare'].fillna(train[train['Fare'].notnull()].median())
    
#     dataset['Fare'] = dataset['Fare'].astype('int64')
# train['CategoricalFare'] = pd.qcut(train['Fare'], 4)
# print (train[['CategoricalFare', 'Survived']].groupby(['CategoricalFare'], as_index=False).mean())

train.columns
train.info()
# train

<class 'pandas.core.frame.DataFrame'>
Int64Index: 891 entries, 0 to 890
Data columns (total 14 columns):
PassengerId    891 non-null int64
Survived       891 non-null int64
Pclass         891 non-null int64
Name           891 non-null object
Sex            891 non-null object
Age            714 non-null float64
SibSp          891 non-null int64
Parch          891 non-null int64
Ticket         891 non-null object
Fare           891 non-null float64
Cabin          204 non-null object
Embarked       891 non-null object
FamilySize     891 non-null int64
IsAlone        891 non-null int64
dtypes: float64(2), int64(7), object(5)
memory usage: 104.4+ KB


## Age


In [10]:
train["Age"][train["Age"].isnull()].size

177

There are many missing values for age so we can fill it with random values

In [11]:
for dataset in full_data:
    age_avg = dataset["Age"][dataset["Age"].notnull()].mean()
    age_std = dataset['Age'].std()
    age_null_count = dataset['Age'].isnull().sum()

    age_rand_list = np.random.randint(age_avg-age_std, age_avg+age_std, size=age_null_count)
    dataset["Age"][dataset["Age"].isnull()] = age_rand_list
    dataset['Age'] = dataset['Age'].astype(int)
#     dataset["CategoricalAge"] = pd.qcut(dataset["Age"], 5)
# #     print(age_null_count)
# print (train[['CategoricalAge', 'Survived']].groupby(['CategoricalAge'], as_index=False).mean())
train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 891 entries, 0 to 890
Data columns (total 14 columns):
PassengerId    891 non-null int64
Survived       891 non-null int64
Pclass         891 non-null int64
Name           891 non-null object
Sex            891 non-null object
Age            891 non-null int64
SibSp          891 non-null int64
Parch          891 non-null int64
Ticket         891 non-null object
Fare           891 non-null float64
Cabin          204 non-null object
Embarked       891 non-null object
FamilySize     891 non-null int64
IsAlone        891 non-null int64
dtypes: float64(1), int64(8), object(5)
memory usage: 104.4+ KB


/home/sharan/anaconda2/envs/py36/lib/python3.6/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


## Name


In [12]:
import re as re
def get_title(name):
	title_search = re.search(' ([A-Za-z]+)\.', name)
	# If the title exists, extract and return it.
	if title_search:
		return title_search.group(1)
	return ""

for dataset in full_data:
    dataset['Title'] = dataset['Name'].apply(get_title)

print(pd.crosstab(train['Title'], train['Sex']))
# train

Sex       female  male
Title                 
Capt           0     1
Col            0     2
Countess       1     0
Don            0     1
Dr             1     6
Jonkheer       0     1
Lady           1     0
Major          0     2
Master         0    40
Miss         182     0
Mlle           2     0
Mme            1     0
Mr             0   517
Mrs          125     0
Ms             1     0
Rev            0     6
Sir            0     1


In [13]:
for dataset in full_data:
    dataset['Title'] = dataset['Title'].replace(['Lady', 'Countess','Capt', 'Col',\
 	'Don', 'Dr', 'Major', 'Rev', 'Sir', 'Jonkheer', 'Dona'], 'Rare')

    dataset['Title'] = dataset['Title'].replace('Mlle', 'Miss')
    dataset['Title'] = dataset['Title'].replace('Ms', 'Miss')
    dataset['Title'] = dataset['Title'].replace('Mme', 'Mrs')

print (train[['Title', 'Survived']].groupby(['Title'], as_index=False).mean())
train.info()

    Title  Survived
0  Master  0.575000
1    Miss  0.702703
2      Mr  0.156673
3     Mrs  0.793651
4    Rare  0.347826
<class 'pandas.core.frame.DataFrame'>
Int64Index: 891 entries, 0 to 890
Data columns (total 15 columns):
PassengerId    891 non-null int64
Survived       891 non-null int64
Pclass         891 non-null int64
Name           891 non-null object
Sex            891 non-null object
Age            891 non-null int64
SibSp          891 non-null int64
Parch          891 non-null int64
Ticket         891 non-null object
Fare           891 non-null float64
Cabin          204 non-null object
Embarked       891 non-null object
FamilySize     891 non-null int64
IsAlone        891 non-null int64
Title          891 non-null object
dtypes: float64(1), int64(8), object(6)
memory usage: 111.4+ KB


# Data cleaning


In [14]:
train.columns

Index(['PassengerId', 'Survived', 'Pclass', 'Name', 'Sex', 'Age', 'SibSp', 'Parch', 'Ticket', 'Fare', 'Cabin', 'Embarked', 'FamilySize', 'IsAlone', 'Title'], dtype='object')

In [15]:

for dataset in full_data:
    # Mapping Sex
    dataset['Sex'] = dataset['Sex'].map( {'female': 0, 'male': 1} )
    
    # Mapping titles
    title_mapping = {"Mr": 1, "Miss": 2, "Mrs": 3, "Master": 4, "Rare": 5}
    dataset['Title'] = dataset['Title'].map(title_mapping)
    dataset['Title'] = dataset['Title'].fillna(0)
    
    # Mapping Embarked
    dataset['Embarked'] = dataset['Embarked'].map( {'S': 0, 'C': 1, 'Q': 2} )
    
#     # Mapping Fare
#     dataset.loc[ dataset['Fare'] <= 7.91, 'Fare'] 						        = 0
#     dataset.loc[(dataset['Fare'] > 7.91) & (dataset['Fare'] <= 14.454), 'Fare'] = 1
#     dataset.loc[(dataset['Fare'] > 14.454) & (dataset['Fare'] <= 31), 'Fare']   = 2
#     dataset.loc[ dataset['Fare'] > 31, 'Fare'] 							        = 3
#     dataset['Fare'] = dataset['Fare']
    
#     # Mapping Age
#     dataset.loc[ dataset['Age'] <= 16, 'Age'] 					       = 0
#     dataset.loc[(dataset['Age'] > 16) & (dataset['Age'] <= 32), 'Age'] = 1
#     dataset.loc[(dataset['Age'] > 32) & (dataset['Age'] <= 48), 'Age'] = 2
#     dataset.loc[(dataset['Age'] > 48) & (dataset['Age'] <= 64), 'Age'] = 3
#     dataset.loc[ dataset['Age'] > 64, 'Age']                           = 4

# Feature Selection
drop_elements = ['PassengerId', 'Name', 'Ticket', 'Cabin', 'SibSp',\
                 'Parch', 'FamilySize']
traindr = train.drop(drop_elements, axis = 1)
# train = train.drop(['CategoricalAge', 'CategoricalFare'], axis = 1)

testdr  = test.drop(drop_elements, axis = 1)

print (train.head(10))

traind = traindr.values
testd  = testdr.values
train.info()

   PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   
5            6         0       3   
6            7         0       1   
7            8         0       3   
8            9         1       3   
9           10         1       2   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    1   22      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    0   38      1      0   
2                             Heikkinen, Miss. Laina    0   26      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    0   35      1      0   
4                           Allen, Mr. William Henry    1   35      0      0   
5                                   Moran, Mr. James    1   19      0      0   
6                            McCarthy, Mr. 

In [57]:
# train
X = traindr[['Pclass', 'Sex', 'Age', 'Fare', 'Embarked', 'IsAlone', 'Title']].values
y = traindr['Survived'].values
from sklearn.cross_validation import train_test_split
[X_train, X_test, y_train, y_test] = train_test_split(X, y, test_size=0.1, random_state=23)

# Ensemble learning


In [58]:
from sklearn.ensemble import VotingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, roc_auc_score

clf1 = LogisticRegression(random_state=1)
clf2 = SVC(random_state=1,probability=True)
clf3 = KNeighborsClassifier(n_neighbors=5, n_jobs=-1)
clf4 = RandomForestClassifier(n_jobs=-1)


pipeline1 = Pipeline([('ssc1', StandardScaler()),
                      ('lr', clf1)])
pipeline2 = Pipeline([('ssc2', StandardScaler()),
                      ('svc', clf2)])
pipeline3 = Pipeline([('ssc3', StandardScaler()),
                      ('knn', clf3)])
# ssc1.fit_transform(X_train, y_train)
# clf1.score(X_test, y_test)


# clf4.fit(X_train, y_train)
# clf4.score(X_test, y_test)

# pipeline3.fit(X_train, y_train)
# pipeline3.score(X_test, y_test)

estimators = [('eclf1', pipeline1), ('eclf2', pipeline2), ('eclf3', pipeline3), ('eclf4', clf4)]

vc = VotingClassifier(estimators = estimators, voting='hard', n_jobs=-1)

vc.fit(X_train, y_train)
vc.score(X_test, y_test)
vc.get_params()

{'eclf1': Pipeline(steps=[('ssc1', StandardScaler(copy=True, with_mean=True, with_std=True)), ('lr', LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
           intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
           penalty='l2', random_state=1, solver='liblinear', tol=0.0001,
           verbose=0, warm_start=False))]),
 'eclf1__lr': LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
           intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
           penalty='l2', random_state=1, solver='liblinear', tol=0.0001,
           verbose=0, warm_start=False),
 'eclf1__lr__C': 1.0,
 'eclf1__lr__class_weight': None,
 'eclf1__lr__dual': False,
 'eclf1__lr__fit_intercept': True,
 'eclf1__lr__intercept_scaling': 1,
 'eclf1__lr__max_iter': 100,
 'eclf1__lr__multi_class': 'ovr',
 'eclf1__lr__n_jobs': 1,
 'eclf1__lr__penalty': 'l2',
 'eclf1__lr__random_state': 1,
 'eclf1__lr__solver': 'liblinear',
 'eclf1__lr__

# GridSearchCV


In [66]:
from sklearn.model_selection import GridSearchCV
param_grid = {
    'eclf1__lr__C': [0.001, 0.01, 0.1, 1.0, 10.0, 100.0],
    'eclf1__lr__penalty': ['l1','l2'],
    'eclf2__svc__C': [0.001, 0.01, 0.1, 1.0, 10.0, 100.0],
    'eclf3__knn__n_neighbors': [4,5,6],
    'voting': ['hard','soft'],
#     'scoring': ['accuracy'],
    'eclf4__max_depth': [1,2]
            }

gs  = GridSearchCV(estimator=vc, param_grid=param_grid, cv=10, verbose =5, n_jobs=-1)
gs.fit(X_train, y_train)
gs.score(X_test,y_test)
# gs.get_params().keys()

Fitting 10 folds for each of 864 candidates, totalling 8640 fits
[CV] eclf1__lr__C=0.001, eclf1__lr__penalty=l1, eclf2__svc__C=0.001, eclf3__knn__n_neighbors=4, eclf4__max_depth=1, voting=hard 


/home/sharan/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/externals/joblib/parallel.py:540: UserWarning: Multiprocessing-backed parallel loops cannot be nested, setting n_jobs=1
  **self._backend_args)


[CV] eclf1__lr__C=0.001, eclf1__lr__penalty=l1, eclf2__svc__C=0.001, eclf3__knn__n_neighbors=4, eclf4__max_depth=1, voting=hard 
[CV] eclf1__lr__C=0.001, eclf1__lr__penalty=l1, eclf2__svc__C=0.001, eclf3__knn__n_neighbors=4, eclf4__max_depth=1, voting=hard 


/home/sharan/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/externals/joblib/parallel.py:540: UserWarning: Multiprocessing-backed parallel loops cannot be nested, setting n_jobs=1
  **self._backend_args)


[CV] eclf1__lr__C=0.001, eclf1__lr__penalty=l1, eclf2__svc__C=0.001, eclf3__knn__n_neighbors=4, eclf4__max_depth=1, voting=hard 


...

[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.765432, total=   1.0s
[CV] eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft 


/home/sharan/anaconda2/envs/py36/lib/python3.6/site-packages/sklearn/externals/joblib/parallel.py:540: UserWarning: Multiprocessing-backed parallel loops cannot be nested, setting n_jobs=1
  **self._backend_args)


[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.825000, total=   0.8s
[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.837500, total=   1.1s
[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.800000, total=   1.0s
[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.850000, total=   0.8s
[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.787500, total=   0.7s
[CV]  eclf1__lr__C=100.0, eclf1__lr__penalty=l2, eclf2__svc__C=100.0, eclf3__knn__n_neighbors=6, eclf4__max_depth=2, voting=soft, score=0.837500, total=   0.8s
[CV]  eclf1__lr__C=100.0, eclf1__lr__pen

[Parallel(n_jobs=-1)]: Done 8640 out of 8640 | elapsed: 16.0min finished


0.84444444444444444

In [67]:
gs.best_params_

{'eclf1__lr__C': 0.001,
 'eclf1__lr__penalty': 'l2',
 'eclf2__svc__C': 10.0,
 'eclf3__knn__n_neighbors': 5,
 'eclf4__max_depth': 1,
 'voting': 'hard'}

In [68]:
gs.best_estimator_

VotingClassifier(estimators=[('eclf1', Pipeline(steps=[('ssc1', StandardScaler(copy=True, with_mean=True, with_std=True)), ('lr', LogisticRegression(C=0.001, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_sta...mators=10, n_jobs=-1, oob_score=False, random_state=None,
            verbose=0, warm_start=False))],
         n_jobs=-1, voting='hard', weights=None)

In [69]:
gs.best_score_

0.82397003745318353

In [80]:
inp = pd.read_csv('testout.csv')
X_trutest=inp.values
X_trutest
# X_trutest = testdr[['Pclass', 'Sex', 'Age', 'Fare', 'Embarked', 'IsAlone', 'Title']].values
y_pred_teat = gs.predict(X_trutest)
stest  = pd.read_csv('test.csv' , header = 0, dtype={'Age': np.float64})
s = np.vstack((stest['PassengerId'].values, y_pred_teat))
s

submit = pd.DataFrame(data =s.transpose(), columns=("PassengerId", "Survived"))
submit
submit.to_csv(path_or_buf='ensemblegridcv.csv', index=False)

ValueError: all the input array dimensions except for the concatenation axis must match exactly